# Explore Eurostat population data.

In this example, we use Copilot for Fabric Data Engineering to load, transform, and save data in a Lakehouse. Let's imagine Contoso Health, a multi-specialty hospital network, wants to expand its services in the EU and wants to analyze projected population data. This example uses the [Eurostat](https://ec.europa.eu/eurostat/web/main/home) (statistical office of the European Union) population projection dataset.

Source: EUROPOP2023 Population on January 1 by age, sex, and type of projection [[proj_23np](https://ec.europa.eu/eurostat/databrowser/product/view/proj_23np?category=proj.proj_23n)], Last updated June 28, 2023.

The following prerequisites should be in place before you start:

- Access to a Microsoft Fabric tenant account with an active subscription. [Create an account](https://azure.microsoft.com/free/).
- Created a Workspace with Fabric enabled: [Create a workspace](/fabric/fundamentals/create-workspaces).
- Created a Lakehouse.
- Imported this notebook and attach it to your Lakehouse.

Chat commands are special commands you can use in your Microsoft Fabric notebooks to interact with Copilot. Here's a list of the most commonly used commands:

| Command | Description |
| ------- | ----------- |
| `%%chat` | Ask questions about the state of your notebook. |
| `%%code` | Code generation for data manipulation or visualization. |
| `%show_chat_history` | Show the chat history. |
| `%clear_chat_history` | Clear the chat history. |
| `%set_output` | Change the default for how magic commands provide output. Choose where to place the generated code, from options like <br>- current cell<br>- new cell<br>- cell output<br>- into a variable<br> |
| `%describe` | Provides summaries and descriptions of loaded dataframes. |
| `%%add_comments` | Add comments to your code. |

This notebook has already been populated with a number %%code commands. Execute each cell indivudally, and wait for the code result to appear. Once ready, execute the code that was generated. Notice Copilot may give slightly different results, so you might need to adapt the prompt or the resulted code.


## Load data

In this first prompt, we will ask Copilot to generate the code to download the data from the eurostat source. We want the data -as is- to be loaded in the our lakehouse. Make sure a lakehouse has been attached. Once you execute the cell, notice below a new cell will be created containing the code to execute.

In [ ]:
%%code

Download the following file from this URL:

https://ec.europa.eu/eurostat/api/dissemination/sdmx/2.1/data/proj_23np$defaultview/?format=TSV
 
Then write the file to the default lakehouse into a folder named temp. Create the folder if it doesn't exist yet.

In [ ]:
#### ATTENTION: AI-generated code can include errors or operations you didn't intend. Review the code in this cell carefully before running it.

import os
import urllib.request

# Define the URL and the destination folder in the lakehouse
url = "https://ec.europa.eu/eurostat/api/dissemination/sdmx/2.1/data/proj_23np$defaultview/?format=TSV"
lakehouse_path = "/lakehouse/default/Files/temp"
file_path = f"{lakehouse_path}/proj_23np.tsv"

# Create the folder if it doesn't exist
if not os.path.exists(lakehouse_path):
    os.makedirs(lakehouse_path)

# Download the file and save it to the specified location
urllib.request.urlretrieve(url, file_path)

print(f"File downloaded and saved to {file_path}")

Once we have the data downloaded to our lakehouse, we want to load it into a dataframe so we can look at the data and start transforming it.

In [ ]:
%%code

Load the file 'Files/temp/proj_23np.tsv' into a spark dataframe.

The fields are separated with a tab.

Show the contents of the DataFrame using display method.

In [ ]:
#### ATTENTION: AI-generated code can include errors or operations you didn't intend. Review the code in this cell carefully before running it.

# Define the file path
file_path = "Files/temp/proj_23np.tsv"

# Load the TSV into a Spark DataFrame
spark_df = spark.read.format("csv").option("header", "true").option("delimiter", "\t").load(file_path)

# Display the contents of the DataFrame
display(spark_df)

## Transform data: split fields

In [ ]:
%%code
Split the first field 'freq,projection,sex,age,unit,geo\TIME_PERIOD' using a comma into 6 separate fields.

In [ ]:
#### ATTENTION: AI-generated code can include errors or operations you didn't intend. Review the code in this cell carefully before running it.

from pyspark.sql.functions import split, col

# Split the first field 'freq,projection,sex,age,unit,geo\TIME_PERIOD' into 6 separate fields
spark_df = spark_df.withColumn("freq", split(col("freq,projection,sex,age,unit,geo\\TIME_PERIOD"), ",").getItem(0)) \
                   .withColumn("projection", split(col("freq,projection,sex,age,unit,geo\\TIME_PERIOD"), ",").getItem(1)) \
                   .withColumn("sex", split(col("freq,projection,sex,age,unit,geo\\TIME_PERIOD"), ",").getItem(2)) \
                   .withColumn("age", split(col("freq,projection,sex,age,unit,geo\\TIME_PERIOD"), ",").getItem(3)) \
                   .withColumn("unit", split(col("freq,projection,sex,age,unit,geo\\TIME_PERIOD"), ",").getItem(4)) \
                   .withColumn("geo", split(col("freq,projection,sex,age,unit,geo\\TIME_PERIOD"), ",").getItem(5))

# Show the updated DataFrame
display(spark_df)

## Transform data: remove fields

In [ ]:
%%code
Remove the fields 'freq', 'age', 'unit'.

In [ ]:
#### ATTENTION: AI-generated code can include errors or operations you didn't intend. Review the code in this cell carefully before running it.

# Remove the fields 'freq', 'age', and 'unit'
spark_df = spark_df.drop('freq', 'age', 'unit')

# Display the updated DataFrame
display(spark_df)

## Transform data: reposition fields

In [ ]:
%%code
The fields 'projection', 'sex', 'geo' should be positioned first.

In [ ]:
#### ATTENTION: AI-generated code can include errors or operations you didn't intend. Review the code in this cell carefully before running it.

# Reorder the columns to place 'projection', 'sex', and 'geo' first
columns = ['projection', 'sex', 'geo'] + [col for col in spark_df.columns if col not in ['projection', 'sex', 'geo']]
spark_df = spark_df.select(columns)

# Display the reordered DataFrame
display(spark_df)

## Transform data: replace values

In [ ]:
%%code
The 'projection' field contains codes that should be replaced with the following values:
    _'BSL' -> 'Baseline projections'.
    _'LFRT' -> 'Sensitivity test: lower fertility'.
    _'LMRT' -> 'Sensitivity test: lower mortality'.
    _'HMIGR' -> 'Sensitivity test: higher migration'.
    _'LMIGR' -> 'Sensitivity test: lower migration'.
    _'NMIGR' -> 'Sensitivity test: no migration'.

In [ ]:
#### ATTENTION: AI-generated code can include errors or operations you didn't intend. Review the code in this cell carefully before running it.

from pyspark.sql.functions import when

# Replace projection codes
spark_df = spark_df.withColumn("projection", 
                               when(spark_df["projection"] == "BSL", "Baseline projections")
                               .when(spark_df["projection"] == "LFRT", "Sensitivity test: lower fertility")
                               .when(spark_df["projection"] == "LMRT", "Sensitivity test: lower mortality")
                               .when(spark_df["projection"] == "HMIGR", "Sensitivity test: higher migration")
                               .when(spark_df["projection"] == "LMIGR", "Sensitivity test: lower migration")
                               .when(spark_df["projection"] == "NMIGR", "Sensitivity test: no migration")
                               .otherwise(spark_df["projection"]))

# Display the updated DataFrame
display(spark_df)

## Transform data: filter data

In [ ]:
%%code
Filter the 'geo' field and remove values 'EA20' and 'EU27_2020' (these are not countries).

In [ ]:
#### ATTENTION: AI-generated code can include errors or operations you didn't intend. Review the code in this cell carefully before running it.

# Filter out 'geo' values 'EA20' and 'EU27_2020'
spark_df = spark_df.filter((spark_df['geo'] != 'EA20') & (spark_df['geo'] != 'EU27_2020'))

# Display the filtered DataFrame
display(spark_df)

In [ ]:
%%code
Filter the 'sex' field and remove 'T' (these are totals).

In [ ]:
#### ATTENTION: AI-generated code can include errors or operations you didn't intend. Review the code in this cell carefully before running it.

# Filter out 'sex' values 'T'
spark_df = spark_df.filter(spark_df['sex'] != 'T')

# Display the filtered DataFrame
display(spark_df)

## Transform data: strip spaces

In [ ]:
%%code
Strip spaces from all field names in the dataframe.

In [ ]:
#### ATTENTION: AI-generated code can include errors or operations you didn't intend. Review the code in this cell carefully before running it.

from pyspark.sql.functions import col

# Strip spaces from all field names
spark_df = spark_df.select([col(column).alias(column.strip()) for column in spark_df.columns])

# Display the updated DataFrame
display(spark_df)

## Transform data: data type conversion

In [ ]:
%%code
Convert the data type of all the year fields to integer.

In [ ]:
#### ATTENTION: AI-generated code can include errors or operations you didn't intend. Review the code in this cell carefully before running it.

from pyspark.sql.functions import col

# Convert the data type of all the year fields to integer
year_columns = [col(column).cast("int") for column in spark_df.columns if column.strip().isdigit()]
spark_df = spark_df.select(*spark_df.columns[:3], *year_columns)

# Display the updated DataFrame
display(spark_df)

## Save data

In [ ]:
%%code
Save the dataframe as a new table named 'Population' in the default lakehouse.

In [ ]:
#### ATTENTION: AI-generated code can include errors or operations you didn't intend. Review the code in this cell carefully before running it.

# Save the DataFrame as a new table named 'Population' in the default lakehouse
spark_df.write.format("delta").saveAsTable("Population")

## Ask questions

In [ ]:
#### ATTENTION: AI-generated code can include errors or operations you didn't intend. Review the code in this cell carefully before running it.

import plotly.graph_objs as go

# Query to get the projected population trends for geo BE from 2022 to 2050
result = spark.sql(
    """
    SELECT `2022`, `2023`, `2025`, `2030`, `2035`,
           `2040`, `2045`, `2050`
    FROM Population
    WHERE geo = 'BE' AND projection = 'Baseline projections'
    """
)
df = result.toPandas()

# Extract data for the line chart
years = df.columns.tolist()
values = df.iloc[0].tolist()

# Create the plot
fig = go.Figure()
fig.add_trace(go.Scatter(x=years, y=values, mode='lines+markers', name='Projected Population'))

# Update layout
fig.update_layout(
    title='Projected Population Trends for Geo BE (Belgium) from 2022 to 2050',
    xaxis_title='Year',
    yaxis_title='Population',
    template='plotly_dark'
)

# Display the plot
fig.show()
